In [2]:
import pandas as pd
import numpy as np

#aca poner el path del dataset de la paot
df_denuncias = pd.read_csv(r'C:\Users\samue\OneDrive\Documents\GitHub\captain_planet_sammy\captain-planet\data\raw\df_paot_con_limpieza.csv', encoding='utf-8')
df_denuncias[["fecha_de_recepcion", "fecha_de_ratificacion", "fecha_de_turno", "fecha_de_admision/radicacion", "fecha_de_conclusion"]] = df_denuncias[["fecha_de_recepcion", "fecha_de_ratificacion", "fecha_de_turno", "fecha_de_admision/radicacion", "fecha_de_conclusion"]].apply(pd.to_datetime, errors = 'coerce')
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_columns', None)

C:\Users\samue\AppData\Local\Temp\ipykernel_18028\3219330318.py:5: DtypeWarning: Columns (22) have mixed types. Specify dtype option on import or set low_memory=False.
  df_denuncias = pd.read_csv(r'C:\Users\samue\OneDrive\Documents\GitHub\captain_planet_sammy\captain-planet\data\raw\df_paot_con_limpieza.csv', encoding='utf-8')
c:\Users\samue\OneDrive\Escritorio\Verano 2022\venv_sabueso\env\lib\site-packages\pandas\core\tools\datetimes.py:1047: UserWarning: Parsing '30/01/2002' in DD/MM/YYYY format. Provide format or specify infer_datetime_format=True for consistent parsing.
  cache_array = _maybe_cache(arg, format, cache, convert_listlike)
c:\Users\samue\OneDrive\Escritorio\Verano 2022\venv_sabueso\env\lib\site-packages\pandas\core\tools\datetimes.py:1047: UserWarning: Parsing '29/04/2002' in DD/MM/YYYY format. Provide format or specify infer_datetime_format=True for consistent parsing.
  cache_array = _maybe_cache(arg, format, cache, convert_listlike)
c:\Users\samue\OneDrive\Escritor

In [3]:
#aca el path del dataset de carpetas de victimas
df_victimas = pd.read_csv(r'C:\Users\samue\OneDrive\Documents\GitHub\captain_planet_sammy\captain-planet\analisis_maltrato_animal\data\clean\df_victimas.csv', encoding='utf-8')



In [ ]:
#esta funcion te regresa un dataframe que tiene de indice todas las colonias (con su respectiva alcaldia), con el numero de denuncias que cuentan con los parametros ingresados vs el numero de carpetas totales x cada colonia

def generar_matriz_carpetas(df_denuncias, materia_denuncia, estatus_denuncia, fecha_de_recepcion_denuncia_ini, fecha_de_recepcion_denuncia_final,  medio_de_recepcion_denuncia):

    df_denuncias = df_denuncias[(df_denuncias['materia']==materia_denuncia)&(df_denuncias['estatus']==estatus_denuncia)&(df_denuncias['fecha_de_recepcion']>fecha_de_recepcion_denuncia_ini)&(df_denuncias['fecha_de_recepcion']<=fecha_de_recepcion_denuncia_final)&(df_denuncias['medio_de_recepcion']==medio_de_recepcion_denuncia)]


    def preparacion_enriquecimiento(df_og, alcaldias_og, colonias_og,  id_denuncia_og):
        df_a_enriquecer = df_og.groupby([alcaldias_og,colonias_og]).count().loc[:,[id_denuncia_og]]

        df_a_enriquecer= df_a_enriquecer.rename(columns={id_denuncia_og:'num_denuncias'})
        return df_a_enriquecer



    
    matriz = preparacion_enriquecimiento(df_denuncias,'alcaldia','colonia','id_denuncia')

    def enriquecimiento(df_a_enriquecer, df_externo, alcaldias_externo, colonias_externo, columnas_de_interes,nombre,tipo):

        if(tipo=='conteo'):
            df_externo_gb = df_externo.groupby([alcaldias_externo, colonias_externo]).count()
        elif(tipo=='suma'):
            df_externo_gb = df_externo.groupby([alcaldias_externo, colonias_externo]).sum()
        else:
            df_externo_gb = df_externo.groupby([alcaldias_externo,colonias_externo]).mean()

        index = 0        

        for columna in columnas_de_interes:

            df_a_enriquecer[nombre[index]] = np.nan

            for i in df_a_enriquecer.index:
                
                datos_externos_temp = df_externo_gb[df_externo_gb.index==i]
                
                if(not datos_externos_temp.empty):    
                    df_a_enriquecer.loc[i[0]].loc[i[1], nombre[index]] = datos_externos_temp.iloc[0][columna]
        
            df_a_enriquecer[nombre[index]] = df_a_enriquecer[nombre[index]].astype('float64')
        
            index = index +1


    enriquecimiento(matriz, df_victimas,'alcaldiahechos','coloniahechos',['idcarpeta'], ['num_carpetas'], 'conteo')

    return matriz


matriz_carpetas = generar_matriz_carpetas(df_denuncias,'Maltrato Animal', 'Concluida','2010-01-01','2020-01-10','Internet')

matriz_carpetas


In [5]:
df_denuncias['anio-mes-admision/radicacion'] = df_denuncias['fecha_de_admision/radicacion'].dt.strftime('%Y-%m')
df_denuncias['anio-mes-conclusion'] = df_denuncias['fecha_de_conclusion'].dt.strftime('%Y-%m')

In [7]:
#esta funcion te regresa una matriz con los parametros tomados en cuenta vs el numero total de denuncias que cumplen con esos parametros

def generar_matriz_parametros(tipo_de_denuncia, materia, anio_mes_admision_radicacion, anio_mes_conclusion, medio_de_recepcion, alcaldia, regimen_propiedad, area_responsable):

    res = pd.DataFrame(columns = ['tipo_de_denuncia','materia','anio-mes-admision/radicacion','anio-mes-conclusion','medio_de_recepcion','alcaldia','regimen_propiedad','area_responsable'], index=range(len(tipo_de_denuncia)*len(materia)*len(anio_mes_admision_radicacion)*len(anio_mes_conclusion)*len(medio_de_recepcion)*len(alcaldia)*len(regimen_propiedad)*len(area_responsable)))
    
   

    index = 0
    for tipo in tipo_de_denuncia:
        for mat in materia:
            for anio_mes_adm in anio_mes_admision_radicacion:
                for anio_mes_con in anio_mes_conclusion:
                    for medio in medio_de_recepcion:
                        for alc in alcaldia:
                            for reg in regimen_propiedad:
                                for area in area_responsable:


                                    res.iloc[index, 0] = tipo
                                    res.iloc[index, 1] = mat
                                    res.iloc[index, 2] = anio_mes_adm
                                    res.iloc[index, 3] = anio_mes_con
                                    res.iloc[index, 4] = medio
                                    res.iloc[index, 5] = alc
                                    res.iloc[index,6] = reg
                                    res.iloc[index, 7] = area
                                    res.iloc[index, 8] = df_denuncias[(df_denuncias['tipo_de_denuncia']==tipo)&
                                                        (df_denuncias['materia']==materia)&(df_denuncias['anio-mes-admision/radicacion']==anio_mes_adm)&
                                                        (df_denuncias['anio-mes-conclusion']==anio_mes_con)&
                                                        (df_denuncias['medio_de_recepcion']==medio)&
                                                        (df_denuncias['alcaldia']==alc)&(df_denuncias['regimen_propiedad']==reg)&(df_denuncias['area_responsable']==area)
                                                        ].shape[0]
                
                                    index = index + 1


    return res



matriz_parametros = generar_matriz_parametros(list(df_denuncias['tipo_de_denuncia'].unique()), list(df_denuncias['materia'].unique()), list(df_denuncias['anio-mes-admision/radicacion'].unique()),list(df_denuncias['anio-mes-conclusion'].unique()),list(df_denuncias['medio_de_recepcion'].unique()),list(df_denuncias['alcaldia'].unique()),list(df_denuncias['regimen_propiedad'].unique()),list(df_denuncias['area_responsable'].unique()))

matriz_parametros




MemoryError: Unable to allocate 57.6 GiB for an array with shape (7726887168,) and data type object

In [3]:
def generar_matriz_parametros(tipo_de_denuncia, materia, medio_de_recepcion, alcaldia, regimen_propiedad, area_responsable):

    res = pd.DataFrame(columns = ['tipo_de_denuncia','materia','medio_de_recepcion','alcaldia','regimen_propiedad','area_responsable', 'num_denuncias'], index=range(len(tipo_de_denuncia)*len(materia)*len(medio_de_recepcion)*len(alcaldia)*len(regimen_propiedad)*len(area_responsable)))
    
   

    index = 0
    for tipo in tipo_de_denuncia:
        for mat in materia:  
            for medio in medio_de_recepcion:
                for alc in alcaldia:
                    for reg in regimen_propiedad:
                        for area in area_responsable:

                            res.iloc[index, 0] = tipo
                            res.iloc[index, 1] = mat
                            res.iloc[index, 2] = medio
                            res.iloc[index, 3] = alc
                            res.iloc[index,4] = reg
                            res.iloc[index, 5] = area
                            res.iloc[index, 6] = df_denuncias[(df_denuncias['tipo_de_denuncia']==tipo)&
                                                (df_denuncias['materia']==mat)&
                                                (df_denuncias['medio_de_recepcion']==medio)&
                                                (df_denuncias['alcaldia']==alc)&(df_denuncias['regimen_propiedad']==reg)&(df_denuncias['area_responsable']==area)
                                                ].shape[0]

                            index = index + 1


    return res



matriz_parametros = generar_matriz_parametros(list(df_denuncias['tipo_de_denuncia'].unique()), list(df_denuncias['materia'].unique()),list(df_denuncias['medio_de_recepcion'].unique()),list(df_denuncias['alcaldia'].unique()),list(df_denuncias['regimen_propiedad'].unique()),list(df_denuncias['area_responsable'].unique()))

matriz_parametros

tipo_de_denuncia                         materia  \
0            Denuncia ciudadana  Áreas Verdes (en Suelo Urbano)   
1            Denuncia ciudadana  Áreas Verdes (en Suelo Urbano)   
2            Denuncia ciudadana  Áreas Verdes (en Suelo Urbano)   
3            Denuncia ciudadana  Áreas Verdes (en Suelo Urbano)   
4            Denuncia ciudadana  Áreas Verdes (en Suelo Urbano)   
...                         ...                             ...   
123643  Investigación de oficio                        Anuncios   
123644  Investigación de oficio                        Anuncios   
123645  Investigación de oficio                        Anuncios   
123646  Investigación de oficio                        Anuncios   
123647  Investigación de oficio                        Anuncios   

            medio_de_recepcion    alcaldia regimen_propiedad  \
0                      Escrita   iztacalco           Pública   
1                      Escrita   iztacalco           Pública   
2                      Escrita   iztacalco           Pública   
3                      Escrita   iztacalco            Social   
4                      Escrita   iztacalco            Social   
...                        ...         ...               ...   
123643  Aplicación móvil (App)  xochimilco           Privada   
123644  Aplicación móvil (App)  xochimilco           Privada   
123645  Aplicación móvil (App)  xochimilco               NaN   
123646  Aplicación móvil (App)  xochimilco               NaN   
123647  Aplicación móvil (App)  xochimilco               NaN   

                                                           area_responsable  \
0                              Subprocuraduría del Ordenamiento Territorial   
1       Subprocuraduría Ambiental, de Protección y Bienestar a los Animales   
2                                                                       NaN   
3                              Subprocuraduría del Ordenamiento Territorial   
4       Subprocuraduría Ambiental, de Protección y Bienestar a los Animales   
...                                                                     ...   
123643  Subprocuraduría Ambiental, de Protección y Bienestar a los Animales   
123644                                                                  NaN   
123645                         Subprocuraduría del Ordenamiento Territorial   
123646  Subprocuraduría Ambiental, de Protección y Bienestar a los Animales   
123647                                                                  NaN   

       num_denuncias  
0                  3  
1                 14  
2                  0  
3                  0  
4                  0  
...              ...  
123643             0  
123644             0  
123645             0  
123646             0  
123647             0  

[123648 rows x 7 columns]

In [6]:
matriz_parametros.to_csv(r'C:\Users\samue\OneDrive\Documents\GitHub\captain_planet_sammy\captain-planet\data\clean\matriz_1.csv')

In [9]:
matriz_parametros['num_denuncias'].sum()

6212

In [13]:
df_denuncias.dropna(subset=['tipo_de_denuncia','materia','medio_de_recepcion','alcaldia','regimen_propiedad','area_responsable'])

Unnamed: 0.1  Unnamed: 0  id_denuncia           estatus  \
0                 0           0            1         Concluida   
1                 1           1            2         Concluida   
2                 2           2            3         Concluida   
3                 3           3            4       No admitida   
4                 4           4            7         Concluida   
...             ...         ...          ...               ...   
56073         56073       56073        56157  En investigación   
56075         56075       56075        56159  En investigación   
56076         56076       56076        56156  En investigación   
56101         56101       56101        56153         Concluida   
56663         56663       56663        56736  En investigación   

         tipo_de_denuncia                    expediente  \
0      Denuncia ciudadana  PAOT-2002/CAJRD-0001-SOT-001   
1      Denuncia ciudadana  PAOT-2002/CAJRD-0002-SPA-001   
2      Denuncia ciudadana  PAOT-2002/CAJRD-0003-SPA-002   
3      Denuncia ciudadana  PAOT-2002/CAJRD-0004-SPA-004   
4      Denuncia ciudadana  PAOT-2002/CAJRD-0006-SPA-003   
...                   ...                           ...   
56073  Denuncia ciudadana       PAOT-2022-1822-SPA-1385   
56075  Denuncia ciudadana       PAOT-2022-1824-SPA-1387   
56076  Denuncia ciudadana       PAOT-2022-1821-SPA-1384   
56101  Denuncia ciudadana       PAOT-2022-1818-SPA-1382   
56663  Denuncia ciudadana       PAOT-2022-2380-SPA-1789   

                              materia fecha_de_recepcion  \
0      Áreas Verdes (en Suelo Urbano)         2002-01-30   
1               Suelo de Conservación         2002-10-04   
2                                Aire         2002-04-29   
3                     Maltrato Animal         2002-04-30   
4                 Uso de Suelo Urbano         2002-02-05   
...                               ...                ...   
56073                 Maltrato Animal         2022-03-31   
56075                 Maltrato Animal         2022-03-31   
56076                           Ruido         2022-03-31   
56101                 Maltrato Animal         2022-03-31   
56663                           Ruido         2022-02-05   

      fecha_de_ratificacion fecha_de_turno fecha_de_admision/radicacion  \
0                2002-01-30     2002-06-02                   2002-06-02   
1                2002-10-04     2002-12-04                   2002-12-04   
2                2002-04-29     2002-04-30                   2002-06-05   
3                2002-04-30     2002-02-05                   2002-02-05   
4                2002-03-05     2002-07-05                   2002-07-05   
...                     ...            ...                          ...   
56073            2022-03-31     2022-01-04                   2022-04-18   
56075            2022-03-31     2022-01-04                   2022-07-04   
56076            2022-03-31     2022-01-04                   2022-04-19   
56101            2022-03-31     2022-01-04                   2022-06-04   
56663            2022-02-05     2022-03-05                   2022-12-05   

      fecha_de_conclusion medio_de_recepcion  \
0              2002-03-14            Escrita   
1              2002-10-06            Escrita   
2              2002-06-24            Escrita   
3              2002-02-05            Escrita   
4              2002-06-20            Escrita   
...                   ...                ...   
56073                 NaT           Internet   
56075                 NaT           Internet   
56076                 NaT           Internet   
56101          2022-12-04           Internet   
56663                 NaT           Teléfono   

                                                                                                  domicilio  \
0                                                                   Calle: AV. SUR No.20 Referencia: PARQUE   
1                                      Calle: PARCELA No.196 BIS Referencia: DE LA T